#**6. gyakorlat - Fluid hálózatok**



##1. Fluid forgalmak

1. Egy hálózatban 3 fluid szerver van, kiszolgálási sebességük rendre $3.0, 3.5, 6.0$. A hálózatban 4 különböző prioritású forgalom van jelen, csökkenő prioritási sorrendben:

    (1) az érkezési rátája $1.6$, és áthalad a 2-es és 3-as szervereken;

	  (2) az érkezési rátája $2.4$, és áthalad mindhárom szerveren;

	  (3) az érkezési rátája $1.3$, és áthalad az 1-es és 3-as szervereken;

	  (4) az érkezési rátája $1.7$, és áthalad a 3-as szerveren.

  Minden forgalomról ütközés esetén instant és tökéletes visszaszabályozást feltételezünk a hálózatba való belépési pontjukig visszamenőleg.

  Számítsuk ki, melyik forgalom mekkora sebességre áll be. Adjuk meg azt is, melyik szervernek mekkora a kihasználtsága.


In [ ]:
import numpy as np

# A szerverek sávszélessége
bw_srv = np.array([3.0, 3.5, 6.0])

# A szerverek száma
n_srv = len(bw_srv)

# A forgalmak érkezési rátája (maximális sávszélesség)
rate_tr = np.array([1.6, 2.4, 1.3, 1.7])

# A forgalmak száma
n_tr = len(rate_tr)

# Az illeszkedési mátrix
A = np.array([[0, 1, 1],
              [1, 1, 1],
              [1, 0, 1],
              [0, 0, 1]])




# A szerverekben fennmaradó szabad sávszélesség az egyes igények kezelése után
rem_bw = bw_srv.copy()

# A forgalmak végső sávszélessége
bw_tr = np.full(n_tr, -1.0)


# Prioritási sorrendben megyünk végig a forgalmakon
for i in range(n_tr):
    # Az egyes szerverekben nem foglalunk többet mint a maradék szabad sávszélsség és az adott igény maximális sávszélessége
    temp_bw = np.minimum(rate_tr[i]*A[i], rem_bw)
    print(f"A(z) {i}. forgalom biztos nem foglalhat többet a szerverekben, mint: {temp_bw}")

    # Csak azokat a szervereket vesszük figyelembe, ahol át is megy a forgalom
    bw_tr[i] = np.min(temp_bw[A[i]>0] )
    print(f"A(z) {i}. forgalom sávszélessége: {bw_tr[i]}\n")
    rem_bw -= bw_tr[i] * A[i]

print("A maradék szabad kapacitás a szerverekben:", rem_bw)
print("A szerverek kihasználtságának vektora:", 1 - rem_bw/bw_srv)

A(z) 0. forgalom biztos nem foglalhat többet a szerverekben, mint: [0.  1.6 1.6]
A(z) 0. forgalom sávszélessége: 1.6

A(z) 1. forgalom biztos nem foglalhat többet a szerverekben, mint: [2.4 1.9 2.4]
A(z) 1. forgalom sávszélessége: 1.9

A(z) 2. forgalom biztos nem foglalhat többet a szerverekben, mint: [1.1 0.  1.3]
A(z) 2. forgalom sávszélessége: 1.1

A(z) 3. forgalom biztos nem foglalhat többet a szerverekben, mint: [0.  0.  1.4]
A(z) 3. forgalom sávszélessége: 1.4000000000000004

A maradék szabad kapacitás a szerverekben: [0. 0. 0.]
A szerverek kihasználtságának vektora: [1. 1. 1.]


2. Egy hálózatban 2 fluid szerver van, kiszolgálási sebességük rendre $2.0, 3.0$. A hálózatban 3 fluid forgalom van jelen, melyek között mindkét szerver WFQ elv alapján osztja ki a sávszélességet, az egyes forgalmak súlyai $(0.5, 0.4, 0.1)$. Az egyes forgalmak jellemzői:

  (1) az érkezési rátája 2.0, és áthalad az 1-es szerveren;

  (2) az érkezési rátája 3.0, és áthalad mindkét szerveren;

  (3) az érkezési rátája 1.0, és áthalad a 2-es szerveren.

  Minden forgalomról ütközés esetén instant és tökéletes visszaszabályozást feltételezünk a hálózatba való belépési pontjukig visszamenőleg.

  Számítsuk ki, melyik forgalom mekkora sebességre áll be. Adjuk meg azt is, melyik szervernek mekkora a kihasználtsága.


In [ ]:
from IPython.display import display, Math
import sympy as sp
from scipy.optimize import linprog

def disp(expr, val=""):
  display(Math(expr + "=" + sp.latex(val)))
  print("\n")

# A szerverek sebessége
mu = np.array([2.0, 3.0])

# A forgalmak érkezési sebessége (maximális sávszélessége)
lam = np.array([2.0, 3.0, 1.0])

# Az igényekhez rendelt WFQ súlyuk
w = np.array([0.5, 0.3, 0.2])

# Numerikus hiba kezelésére
eps = 10**-7

# Illeszkedési mátrix
A = np.array([[1, 0],
              [1, 1],
              [0, 1]])

# Forgalmak és szerverek száma
n_tr, n_srv = A.shape

# Még nem véglegesített, "aktív" forgalmak jelzése
a = np.ones(n_tr)

# Forgalmak aktuálisan elfogadott sávszélessége
lam_c = np.zeros(n_tr)

# A számolás iterációinak száma
n = 1

# Addig megyünk, amíg minden forgalmat nem véglegesítünk (vagy az iterációk száma irreálisan nagy lesz)
while max(a) > 0 and n < 100:
    print(f"---------------------------\n{n}. iteráció\n---------------------------\n")
    # Lineáris programozási feladatként írjuk fel a feladatot
    # -1*h minimalizálása a cél
    obj = np.array([-1])

    # Bevezetjük a "w * a" (elemenkénti szorzat) mennyiséget
    w_a = w * a

    # A konstansokat az egyenlőtlenségekben jobbra rendezzük
    # Az egyenlőtlenségek bal oldala
    lhs_ineq = np.hstack((w_a , w_a @ A)).reshape(-1,1)
    # Az egyenlőtlenségek jobb oldala
    rhs_ineq = np.hstack((lam - lam_c, mu-lam_c @ A))

    # Az alapértelmezett határok is (0, None), de kiírjuk a biztonság kedvéért
    bounds_ineq = (0, None)

    # Optimalizáljuk h értékét
    h = linprog(c=obj, A_ub=lhs_ineq, b_ub=rhs_ineq, bounds=bounds_ineq).x

    # Kiszámoljuk az új lam_c értékeket a megfelelő súlyú növelések után
    lam_c += w_a * h


    disp("h", h)
    disp("\lambda_c", lam_c)
    disp("\mu - \lambda_c A", mu-lam_c @ A)

    # Egy forgalmat akkor tekintünk inaktívnak, ha:
    # 1. eléri a maximális sebességét
    cond1 = np.abs(lam_c - lam) < eps
    print(f"Elérte a forgalom a maximális sávszélességét? {cond1}\n")

    # 2. egy olyan szerveren megy át, melynek nem maradt szabad sávszélessége
    cond2_0 = np.abs(mu-lam_c @ A) < eps
    cond2 = A @ cond2_0

    print(f"A forgalomhoz tartozó minden szerverben van még szabad kapacitás? {cond2}\n")

    a = 1 - (cond1 | cond2)

    print(f"A forgalmak aktivitásának vektora: {a}")

    n += 1

print("\n----------------------------------------------------------")
print("----------------------------------------------------------\n")
print("A forgalmak elfogadott sebessége:")
disp("\\lambda_c", lam_c)
print("A szerverek kihasználtságának vektora:")
disp("\\rho", 1 - (mu-lam_c @ A)/mu)

---------------------------
1. iteráció
---------------------------



<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>



Elérte a forgalom a maximális sávszélességét? [False False False]

A forgalomhoz tartozó minden szerverben van még szabad kapacitás? [1 1 0]

A forgalmak aktivitásának vektora: [0 0 1]
---------------------------
2. iteráció
---------------------------



...

<IPython.core.display.Math object>



Elérte a forgalom a maximális sávszélességét? [False False  True]

A forgalomhoz tartozó minden szerverben van még szabad kapacitás? [1 1 0]

A forgalmak aktivitásának vektora: [0 0 0]

----------------------------------------------------------
----------------------------------------------------------

A forgalmak elfogadott sebessége:


<IPython.core.display.Math object>



A szerverek kihasználtságának vektora:


<IPython.core.display.Math object>

3. Adott egy $C=5$ kapacitású fluid csatorna. Kétféle forgalmi osztályból markovi módon érkeznek fix sávszélességű (constant bit rate, CBR) forgalmak; az $i$-edik osztályból az érkezési ráta $\lambda_i$, a távozási ráta $\mu_i$, egy forgalom sávszélessége $c_i$. A két forgalmi osztály jellemzői:
$$c_1=1, \lambda_1=1,\mu_1=1, \qquad c_2=3, \lambda_2=1,\mu_2=2.$$
Ha egy forgalom az érkezés pillanatában befér a csatornába, beengedjük, egyébként eldobjuk.

  Mekkora a csatornában a forgalom hosszú távú átlaga?

  Az egyes forgalmi osztályokból a forgalmak mekkora részét dobjuk el érkezéskor?

  Az idő mekkora részében van a csatorna teljesen kihasználva?

In [ ]:
# A különböző osztályú forgalmak sávszélessége
cv = np.array([1, 3])

# A forgalmak érkezési rátája
lam = np.array([1.0, 1.0])

# A forgalmak távozási rátája
mu = np.array([1.0, 2.0])

# A forgalmi osztályok száma
n = len(cv)

# A csatorna kapacitása
C = 4

# Mivel különböző a rendszer különböző állapotai közti legkisebb összforgalom különbség 1.0, ezért a lépésköz is 1.0, így ezzel nem kell normalizálni
# cd = 1.0

# Összes sávszélesség szempontjából C+1 különböző állapothalmaz van: 0, 1,..., C
nc = C + 1
v_st = np.zeros(nc)
v_st[0] = 1

# A Kauffman-Roberts képlet szerint végigmegyünk az összes állapothalmazon
for c in range(1, nc):
    # Kiszámoljuk a stacionárius vektor elemeit rekurzívan...
    v_st[c] = sum([(lam[i]*cv[i])/(mu[i]*c) * (v_st[c-cv[i]] if c-cv[i] >= 0 else 0) for i in range(n)])

#...majd normalizálunk
v_st /= np.sum(v_st)

print(f"A stacionárius eloszlás:")
disp("v_{st}", v_st)

print("A csatornában a forgalom hosszú távú átlaga:")
disp("\sum_{c=0}^{C}c \cdot v_{st}(c)", v_st @ range(nc))

# Összeadjuk azon állapotok valószínűségét, amikor már nem férne be még egy adott osztályú igény
print("Az 1-es osztályú igények dobási valószínűsége:", np.sum(v_st[-cv[0]:]))
print("A 2-es osztályú igények dobási valószínűsége:", np.sum(v_st[-cv[1]:]))

print("\nA csatorna az idő mekkora részében van kihasználva?")
disp("v_{st}(4)", v_st[-1])

4. Egy csatorna kapacitása $C=$ 13 Mbps. A csatornába egyfajta adaptív forgalom érkezik, a forgalmak érkezési rátája $\lambda=$ 2/s. Egy forgalom EXP(1/s) ideig tart a kapott sávszélességtől függetlenül; a sávszélesség-korlátai $c_{\min}=$ 2 és $c_{\max}=$ 3 Mbps.

  A csatornában egyszerre bent lévő forgalmak mind egyforma sávszélességet kapnak. Amíg az egy forgalomra jutó sávszélesség nem csökken $c_{\min}$ alá, addig az érkező forgalmakat beengedjük, egyébként érkezéskor eldobjuk.

  (a) Mekkora az érkezéskor eldobás valószínűsége?

  (b) Számítsuk ki az egy forgalom által kapott átlagos sávszélességet.

In [ ]:
# A csatorna kapacitása
C = 13

# A forgalmak érkezési rátája
lam = 2

# A forgalmak távozási rátája
mu = 1

# Forgalmankénti minimális és maximális sávszélesség
c_min, c_max = 2, 3

# A csatornában lévő igények maximális száma
n_max = int(C/c_min)

# A stacionárius eloszlás képletének megfelelően
v_st = np.array([np.prod([lam/(k*mu) if k>0 else 1 for k in range(0, nt+1)]) for nt in range(n_max+1)])
v_st /= np.sum(v_st)

print("A stacionárius eloszlás:")
disp("v_{st}=\\frac{\lambda/(k\mu)}{\sum_{n=0}^{n_{max}}\lambda/(k\mu)}", v_st)

print(f"Az eldobás valószínűsége: {v_st[-1]}\n")

print("Az egy forgalom által kapott átlagos sávszélesség:")
disp("\\bar{c}=\\frac{\sum_{n=0}^{n_{max}}v_{st}(n) \\text{ min}(C, n_{max})}{\sum_{n=0}^{n_{max}}n v_{st}(n)}",
     sum([v_st[nt] * min(C, nt*c_max) for nt in range(n_max+1)]) / (range(n_max+1) @ v_st)
    )